# EU - finanční sankce

Více informací na : https://data.europa.eu/data/datasets/consolidated-list-of-persons-groups-and-entities-subject-to-eu-financial-sanctions?locale=cs

## Import knihoven a nastavení

In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

pd.set_option('display.max_rows', None)  # Chceme vidět všechny řádky
pd.set_option('display.max_columns', None)  # Chceme vidět všechny sloupce

## Načtení dat - sankce

In [ ]:
sankce = pd.read_csv('https://webgate.ec.europa.eu/fsd/fsf/public/files/csvFullSanctionsList_1_1/content?token=dG9rZW4tMjAxNw', 
  sep=';', 
  usecols=('Entity_LogicalId', 'Entity_Regulation_EntryIntoForceDate',
    'Citizenship_CountryIso2Code', 'Entity_SubjectType_ClassificationCode'),  # Jen vybrané sloupce
  parse_dates=['Entity_Regulation_EntryIntoForceDate',]  # Tento sloupec načteme jako datum
)
sankce.head()

## Načtení dat - kódy zemí

In [ ]:
zeme = pd.read_csv('https://datahub.io/core/country-list/r/data.csv')
zeme.head()

## Vymaž řádky, kde chybí Citizenship_CountryIso2Code

In [ ]:
sankce.dropna(
  subset=['Citizenship_CountryIso2Code'], 
  inplace=True
)

## Vymaž duplicity pro sloupec Entity_LogicalId

In [ ]:
sankce.drop_duplicates(
  subset='Entity_LogicalId', 
  keep='first',  # ponech pouze 1. výskyt
  inplace=True
)

## Vytvoř sloupec Rok (kdy vstoupila sankce v platnost)

In [ ]:
sankce['Year'] = sankce['Entity_Regulation_EntryIntoForceDate'].dt.year

## Přidej ke kódům názvy zemí

In [ ]:
sankce_zeme = pd.merge(sankce, zeme, 
  how='inner',  # Inner join
  left_on='Citizenship_CountryIso2Code',
  right_on='Code'
)

## Kontingenční tabulka

In [ ]:
cols = ['Name', 'Year', 'Entity_LogicalId']
flt1 = sankce_zeme['Entity_SubjectType_ClassificationCode'] == 'person'  # Pouze řádky, týkající se osob

kont_tabulka = pd.pivot_table(sankce_zeme.loc[flt1, cols],
  index=cols[0:2],  # První dva sloupce = Name, Year
  values='Entity_LogicalId',
  fill_value=0,  # Prázdné hodnoty nahraď nulou
  aggfunc='count',  # Použij agregační funkci Count
).reset_index()  # Udělej z indexů sloupce

kont_tabulka.head()

## Heatmap

In [ ]:
sns.set(font_scale=2)  # Zvětšíme velikost písma
px = 1/plt.rcParams['figure.dpi']  # zjistíme velikost pixelu v palcích
f, ax = plt.subplots(figsize=(1600*px, 3200*px))  # Nadefinujeme velikost grafu v pixelech

sns.heatmap(kont_tabulka.pivot('Name', 'Year', 'Entity_LogicalId'),
  cmap='Purples',  # Barevné schéma vhodné pro kvantitativní data
  annot=True,  # Chceme zobrazit hodnoty
  fmt='.0f',  # Formát čísla
  cbar=False,  # Nechceme zobrazit barevný pruh na straně
  ax=ax  # Použijeme nastavení pro vizualizaci
)